In [ ]:
import nltk
nltk.download("brown")
nltk.download("webtext")
nltk.download("reuters")
nltk.download("punkt_tab")
from nltk.corpus import brown, webtext, reuters
brown_corpus = brown.sents()
brown_corpus = [" ".join(sentence) for sentence in brown_corpus]
brown_corpus = ["<s> " + sentence + " </s>" for sentence in brown_corpus][:5000]
webtext_corpus = webtext.sents()
webtext_corpus = [" ".join(sentence) for sentence in webtext_corpus]
webtext_corpus = ["<s> " + sentence + " </s>" for sentence in webtext_corpus][:5000]
reuters_corpus = reuters.sents()
reuters_corpus = [" ".join(sentence) for sentence in reuters_corpus]
reuters_corpus = ["<s> " + sentence + " </s>" for sentence in reuters_corpus][:5000]

[nltk_data] Downloading package brown to /root/nltk_data...
[nltk_data]   Unzipping corpora/brown.zip.
[nltk_data] Downloading package webtext to /root/nltk_data...
[nltk_data]   Unzipping corpora/webtext.zip.
[nltk_data] Downloading package reuters to /root/nltk_data...
[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.


In [ ]:
from collections import Counter
from nltk.tokenize import word_tokenize
import math

#creates the unigram
def unigram_create(corpus):
   unigram_counter = Counter()
   for sentence in corpus:
      for word in word_tokenize(sentence):
         unigram_counter[word] += 1
   return unigram_counter

def unigram_probability(word, unigram_counter):
  #we are doing this so that we do not have issues during perplexity and is called lapse normalization
   if word not in unigram_counter:
      return 1/(sum(unigram_counter.values()) + len(unigram_counter.values()))

   #word = word.strip().lower()
   return (unigram_counter[word] +1) / (sum(unigram_counter.values()) + len(unigram_counter.values())) #adding one count for a new word in numerator


In [ ]:
unigram = unigram_create(brown_corpus)
print(unigram)

print("Unigram Probablity for the word 'the' : " , unigram_probability("the", unigram))

Counter({'<': 10000, '>': 10000, 'the': 6058, ',': 5506, 's': 5000, '/s': 5000, '.': 4526, 'of': 3128, 'and': 2326, 'to': 2311, 'a': 2138, 'in': 2017, '``': 1503, 'for': 1023, 'that': 890, 'The': 888, 'is': 832, 'was': 796, "'s": 724, 'on': 704, 'at': 618, 'with': 607, 'be': 582, 'by': 536, 'as': 528, 'he': 501, 'his': 449, 'it': 440, 'will': 421, 'said': 408, 'from': 372, 'are': 359, 'has': 342, 'an': 329, ';': 318, 'not': 317, '--': 313, 'had': 305, 'have': 302, 'who': 292, 'this': 279, 'would': 275, 'which': 269, 'were': 261, 'Mrs.': 251, 'been': 241, 'their': 234, 'they': 230, '$': 228, 'I': 219, 'He': 217, 'one': 203, 'its': 199, 'or': 197, 'but': 197, 'Mr.': 196, 'more': 189, 'all': 176, ')': 175, 'up': 174, 'out': 173, '(': 172, 'last': 169, 'other': 167, 'two': 167, 'year': 164, 'new': 158, 'A': 156, 'than': 153, ':': 152, 'It': 146, 'first': 146, 'about': 145, "'": 142, 'there': 139, 'when': 137, 'In': 135, 'after': 132, 'into': 130, 'home': 129, 'But': 126, 'can': 125, 'also'

In [ ]:
def bigram_create(corpus):
  bigram_counter = Counter()
  for sentence in corpus:
    words = word_tokenize(sentence)
    for i in range(len(words) - 1): # we did -1 because we are looking at 2 words at a time
      bigram_counter[(words[i], words[i + 1])] += 1 #increasing count everytime we find it
  return bigram_counter

def bigram_fromSentence_create(sentence):
    words = word_tokenize(sentence)
    biagrams_list = []
    for i in range(len(words) - 1): # we did -1 because we are looking at 2 words at a time
      biagrams_list.append((words[i], words[i + 1]))
    return biagrams_list

In [ ]:
# This function takes in a word and the unigram dictionary
# It implements Laplace smoothing by adding 1 to the count
def unigramCounter(word, unigram):
        if word in unigram:
            return (unigram[word] + 1) # Laplace smoothing: adding one to avoid zero probabilities
        return 1  # Laplace smoothing: return 1 for unseen words

# This function takes two words and the bigram dictionary
# It also implements Laplace smoothing by adding 1 to the count
def bigramCounter(word1, word2, bigram):
        if (word1, word2) in bigram:
            return (bigram[(word1, word2)] + 1) # Laplace smoothing: adding one to avoid zero probabilities
        return 1  # Laplace smoothing: return 1 for unseen bigrams

# Function to calculate conditional probability P(word2|word1) using Laplace smoothing
def conditional_prob_bg(word1, word2, biagrams, unigrams):
    word1 = word1.strip()
    word2 = word2.strip()
    unigramCount = unigramCounter(word1, unigrams)  # Get smoothed count of word1
    bigramCount = bigramCounter(word1, word2, biagrams)  # Get smoothed count of (word1, word2)

    # If word1 is not in the unigrams dictionary, add the vocabulary size to the denominator
    # This is an implementation of Laplace smoothing where the denominator needs
    # to account for the vocabulary size
    if word1 not in unigrams:
        unigramCount += len(unigram.values())

    # Calculate conditional probability with Laplace smoothing: P(word2|word1) = (count(word1,word2) + 1) / (count(word1) + V)
    # where V is the vocabulary size (implicitly handled in the unigram counter function)
    return bigramCount / unigramCount

In [ ]:
bigram = bigram_create(brown_corpus)
print(bigram)

bigram_fromSentence_create("This is a test")

unigram = unigram_create(brown_corpus)
conditional_prob_bg("This", "one", bigram, unigram)
conditional_prob_bg("one", "this", bigram, unigram)


#print("Unigram Probablity for the word 'the' : " , unigram_probability("the", unigram))

Counter({('<', 's'): 5000, ('s', '>'): 5000, ('<', '/s'): 5000, ('/s', '>'): 5000, ('.', '<'): 4376, ('of', 'the'): 914, ('>', 'The'): 808, ('in', 'the'): 590, (',', 'and'): 399, (',', 'the'): 388, ('``', '.'): 307, ('to', 'the'): 297, ('>', '``'): 284, ('on', 'the'): 260, ('for', 'the'): 237, ('>', 'He'): 207, ('``', ','): 202, ('at', 'the'): 187, ('will', 'be'): 164, (';', ';'): 159, (';', '<'): 159, ('that', 'the'): 153, ('and', 'the'): 153, ('with', 'the'): 145, (',', 'who'): 131, ('>', 'It'): 128, (',', 'a'): 127, ('>', 'In'): 124, ('>', 'A'): 123, (',', 'he'): 123, ('by', 'the'): 122, ('to', 'be'): 122, ('in', 'a'): 121, ('of', 'a'): 121, ('>', 'But'): 118, ('from', 'the'): 111, ('for', 'a'): 102, (',', 'but'): 101, (',', '``'): 99, ('has', 'been'): 99, ('as', 'a'): 86, ('is', 'a'): 84, (',', 'in'): 83, ('with', 'a'): 79, ('said', '.'): 77, (',', 'which'): 75, ('>', '--'): 75, ('would', 'be'): 74, (',', 'Mrs.'): 73, ('to', 'a'): 73, ('>', 'Mr.'): 73, ('said', ','): 72, ('the', 'f

0.012987012987012988

In [ ]:
def predictNextWordBigram(word, bigram):
    word = word.strip()
    wordCount = {w2: count for (w1, w2), count in bigram.items() if w1 == word}

    if not wordCount:
        print("There are no bigrams")
        return
    next_word = max(wordCount, key=wordCount.get)
    return next_word

In [ ]:
predictNextWordBigram("any", bigram)

'other'

In [ ]:
def predictnWordsBigram(word, bigram, n):
    word = word.strip()
    sentence = word + ' '
    for i in range(n):
      wordCount = {w2 : count for (w1, w2), count in bigram.items() if w1 == word }
      if not wordCount:
        print("There are no Bigrams")
        return sentence
      next_word = max(wordCount, key = wordCount.get)
      sentence += next_word + ' '

      word = next_word

    return sentence

In [ ]:
print(predictnWordsBigram("any", bigram, 5))
print(predictnWordsBigram("this", bigram, 10))

any page is not work in 
this page is not work in the page is not work 


In [ ]:
def trigram_create(corpus):
  trigram_counter = Counter()
  for sentence in corpus:
    words = word_tokenize(sentence)
    for i in range(len(words) - 2): # we did -2 because we are looking at 3 words at a time
      trigram_counter[(words[i], words[i + 1], words[i + 2])] += 1 #increasing count everytime we find it
  return trigram_counter

def trigram_fromSentence_create(sentence):
    words = word_tokenize(sentence)
    trigrams_list = []
    for i in range(len(words) - 2): # we did -1 because we are looking at 2 words at a time
      trigrams_list.append((words[i], words[i + 1], words[i + 2]))
    return trigrams_list


In [ ]:
trigram = trigram_create(brown_corpus)
print(trigram)

trigram_fromSentence_create("this is a test")

Counter({('<', 's', '>'): 5000, ('<', '/s', '>'): 5000, ('.', '<', '/s'): 4376, ('s', '>', 'The'): 808, ('``', '.', '<'): 307, ('s', '>', '``'): 284, ('s', '>', 'He'): 207, (';', ';', '<'): 159, (';', '<', '/s'): 159, ('s', '>', 'It'): 128, ('s', '>', 'In'): 124, ('s', '>', 'A'): 123, ('s', '>', 'But'): 118, ('said', '.', '<'): 77, ('s', '>', '--'): 75, ('s', '>', 'Mr.'): 73, ('s', '>', 'They'): 66, ('s', '>', 'This'): 62, ('s', '>', 'There'): 59, ('s', '>', 'Mrs.'): 57, ('?', '?', '<'): 53, ('?', '<', '/s'): 53, (',', 'he', 'said'): 50, (':', '<', '/s'): 43, ('the', 'United', 'States'): 43, ('s', '>', 'I'): 42, ('s', '>', 'And'): 42, ('>', '``', 'I'): 41, ('Mr.', 'and', 'Mrs.'): 40, ('one', 'of', 'the'): 39, (',', 'and', 'the'): 39, ('s', '>', 'At'): 39, ('year', '.', '<'): 38, ('``', ',', 'he'): 38, ('>', 'In', 'the'): 36, ('>', 'It', 'was'): 36, ('s', '>', 'When'): 35, ('s', '>', 'She'): 35, (')', '<', '/s'): 34, ('s', '>', 'As'): 34, ('>', 'It', 'is'): 33, ('members', 'of', 'the'):

[('this', 'is', 'a'), ('is', 'a', 'test')]

In [ ]:
# Function to count bigrams with Laplace smoothing
def bigramCounter(word1, word2, bigram):
        if (word1, word2) in bigram:
            return (bigram[(word1, word2)] + 1) # Laplace smoothing: adding one to avoid zero probabilities
        return 1  # Laplace smoothing: return 1 for unseen bigrams

# Function to count trigrams with Laplace smoothing
def trigramCounter(word1, word2, word3, trigram):
        if (word1, word2, word3) in trigram:
            return (trigram[(word1, word2, word3)] + 1) # Laplace smoothing: adding one to avoid zero probabilities
        return 1  # Laplace smoothing: return 1 for unseen trigrams

# Function to calculate conditional probability P(word3|word1,word2) using Laplace smoothing
def conditional_prob_tg(word1, word2, word3, biagrams, trigrams, unigram):
    word1 = word1.strip()
    word2 = word2.strip()
    # unigramCount = unigramCounter(word1, unigrams)

    bigramCount = bigramCounter(word1, word2, biagrams)  # Get smoothed count of (word1, word2)
    trigramCount = trigramCounter(word1, word2, word3, trigrams)  # Get smoothed count of (word1, word2, word3)

    # If the bigram (word1, word2) is not in the bigrams dictionary, add the vocabulary size to the denominator
    # This is part of the Laplace smoothing for conditional probability calculation
    if (word1, word2) not in biagrams:
        bigramCount += len(unigram.values())  # Adds vocabulary size to denominator for unseen contexts

    # Calculate conditional probability with Laplace smoothing: P(word3|word1,word2) = (count(word1,word2,word3) + 1) / (count(word1,word2) + V)
    # where V is the vocabulary size (handled in the previous lines)
    return trigramCount / bigramCount

In [ ]:
unigram = unigram_create(webtext_corpus)
bigram = bigram_create(webtext_corpus)
trigram = trigram_create(webtext_corpus)
#bigram = bigram_create(brown_corpus)
print(conditional_prob_tg("The", "first","one", bigram, trigram, unigram))
print(conditional_prob_tg("this", "is", "a" , bigram, trigram, unigram))


0.3333333333333333
0.21739130434782608


In [ ]:
def predictNextWordTrigram(word1, word2, trigram):
    word1 = word1.strip()
    word2 = word2.strip()
    wordCount = {w3: count for (w1, w2, w3), count in trigram.items() if w1 == word1 and w2 == word2}

    if not wordCount:
        print("There are no trigrams")
        return
    next_word = max(wordCount, key=wordCount.get)
    return next_word

In [ ]:
print(predictNextWordTrigram("any", "other", trigram))
print(predictNextWordTrigram("there", "is", trigram))

site
no


In [ ]:
def predictnWordsTrigram(word1, word2, trigram, n):
    word1 = word1.strip()
    word2 = word2.strip()
    sentence = word1 + ' ' + word2 + ' '
    for i in range(n):
      wordCount = {w3 : count for (w1, w2, w3), count in trigram.items() if w1 == word1 and w2 == word2}
      if not wordCount:
        print("There are no Trigrams")
        return sentence
      next_word = max(wordCount, key = wordCount.get)
      sentence += next_word + ' '

      word1 = word2
      word2 = next_word

    return sentence

In [ ]:
predictnWordsTrigram("the", "first", trigram, 8)

'the first time in a new tab `` button in '

In [ ]:
predictnWordsTrigram("this", "is", trigram, 10)

'this is the last open window in the bookmarks toolbar folder in '

## **This is Part 4:**



In [ ]:
bigrams_brown = bigram_create(brown_corpus)
bigrams_webtext = bigram_create(webtext_corpus)
#bigrams_reuters = bigram_create(reuters_corpus)

trigrams_brown = trigram_create(brown_corpus)
trigrams_webtext = trigram_create(webtext_corpus)
#trigrams_reuters = trigram_create(reuters_corpus)

In [ ]:
print(predictnWordsBigram("The", bigrams_webtext, 10))
print(predictnWordsBigram("The", bigrams_brown, 10))

print(predictnWordsBigram("One", bigrams_webtext, 10))
print(predictnWordsBigram("One", bigrams_brown, 10))

print(predictnWordsBigram("Some", bigrams_webtext, 10))
print(predictnWordsBigram("Some", bigrams_brown, 10))

The `` in the page is not work in the page 
The President Kennedy 's first time . < s > The 
One gestures Focus not work in the page is not work 
One of the first time . < s > The President 
Some data in the page is not work in the page 
Some of the first time . < s > The President 


In [ ]:
print(predictnWordsTrigram("The", "first", trigrams_webtext, 10))
print(predictnWordsTrigram("The", "first", trigrams_brown, 10))

print(predictnWordsTrigram("One", "of", trigrams_webtext, 10))
print(predictnWordsTrigram("One", "of", trigrams_brown, 10))

print(predictnWordsTrigram("These", "are", trigrams_webtext, 10))
print(predictnWordsTrigram("These", "are", trigrams_brown, 10))

The first letter is typed Ability to set future cookies `` should 
The first of the American League 's 1961 expansion to the public 
One of the page is loading a page with flash plugin when 
One of the American League 's 1961 expansion to the public schools 
These are nice and we will attend to your posts `` page 
These are the most recent being Jimmy Durante and Phil Silvers . 


# **Perplexity :**

In [ ]:
import numpy as np
def bigramPreplexityScore(sentence, unigrams, bigrams):
        words = word_tokenize(sentence)
        lengthWords = len(words)
        probabilities = []

        # since we cant do bigram probability for the first token, we are appending unigram probability.
        #this takes care of the first token
        probabilities.append(unigram_probability(words[0], unigrams))

        #in the for loop, you can see that we are doing conditional probability.
        #this following code takes care of the rest of the tokens.
        for i in range(1,len(words)-1):
            cond_prob = conditional_prob_bg(words[i], words[i+1], bigrams, unigrams)
            probabilities.append(cond_prob)
        #print(probabilities)

        logProbabilities = np.log(probabilities)

        perplexity = (-1/lengthWords) * (sum(logProbabilities))

        return np.exp(perplexity)

In [ ]:
def TrigramPreplexityScore(sentence, trigrams, bigrams, unigrams):
        words = word_tokenize(sentence)
        lengthWords = len(words)

        probabilities = []
        # since we cant do trigram probability for the first two tokens, we are appending unigram probability.
        #this takes care of the first and second tokens
        probabilities.append(conditional_prob_bg(words[0], words[1], bigrams, unigrams))

        #in the for loop, you can see that we are doing conditional probability.
        #this following code takes care of the rest of the tokens.
        for i in range(1,len(words)-2):
            cond_prob = conditional_prob_tg(words[i], words[i+1], words[i+2],bigrams, trigrams, unigrams)
            probabilities.append(cond_prob)

        logProbabilities = np.log(probabilities)

        perplexity = (-1/lengthWords) * (sum(logProbabilities))

        return np.exp(perplexity)

In [ ]:
unigram = unigram_create(brown_corpus)
bigrams = bigram_create(brown_corpus)
print(bigramPreplexityScore("Yeo dgr kje", unigram, bigrams))
print(bigramPreplexityScore("Some of them", unigram, bigrams))
print(bigramPreplexityScore("The first one", unigram, bigrams))

1311.4695456244895
104.85702081217715
23.38876459973305


In [ ]:
unigrams = unigram_create(brown_corpus)
trigrams = trigram_create(brown_corpus)
bigrams = bigram_create(brown_corpus)
print(TrigramPreplexityScore("The first one", trigrams, bigrams, unigrams))
print(TrigramPreplexityScore("Some of them are not that great but it's okay because ", trigrams, bigrams, unigrams))
print(TrigramPreplexityScore("sdkj sdhe ksdjhf eufeb kaerh akeh skfjh", trigrams, bigrams, unigrams))

4.323508912847497
145.28337569670262
941.9490224204435


# **Report Part 2 Test code: **

In [ ]:
def AveragePerpBigram(indexs, bigrams, unigrams, corpus):
    perplixity = 0
    for indx in indexs:
        perplixity += bigramPreplexityScore(corpus[indx], unigram, bigrams)
    return perplixity / len(indexs)

def AveragePerpTri(indexs, trigrams, bigrams, unigrams, corpus):
    perplixity = 0
    for indx in indexs:
        perplixity +=  TrigramPreplexityScore(corpus[indx], trigrams, bigrams, unigrams)

    return perplixity / len(indexs)

In [ ]:
import random

print("Average Perplexity on Reuters, by picking 25 random sentences: ")
indexes = random.sample(range(len(reuters_corpus)), 25)

unigram_brown = unigram_create(brown_corpus)
unigram_webtext = unigram_create(webtext_corpus)

bigrams_brown = bigram_create(brown_corpus)
bigrams_webtext = bigram_create(webtext_corpus)
#bigrams_reuters = bigram_create(reuters_corpus)

trigrams_brown = trigram_create(brown_corpus)
trigrams_webtext = trigram_create(webtext_corpus)
#trigrams_reuters = trigram_create(reuters_corpus)

print(f"Brown BiGram: {AveragePerpBigram(indexes, bigrams_brown, unigram_brown, reuters_corpus )}")

print(f"WebText BiGram : {AveragePerpBigram(indexes, bigrams_webtext ,unigram_webtext, reuters_corpus)}")

print(f"Brown TriGram: {AveragePerpTri(indexes, trigrams_brown,  bigrams_brown, unigram_brown, reuters_corpus )}")
print(f"WebText TriGram : {AveragePerpTri(indexes, trigrams_webtext, bigrams_webtext ,unigram_webtext, reuters_corpus)}")

Average Perplexity on Reuters, by picking 25 random sentences: 
Brown BiGram: 88.33849195368103
WebText BiGram : 108.08843276263116
Brown TriGram: 586.8239556610426
WebText TriGram : 925.6131098961771
